In [15]:
import pandas as pd
import seaborn as sns
import os
import matplotlib.pyplot as plt
from pandas.errors import EmptyDataError

In [16]:
agg_df = pd.DataFrame()

workdir_path = 'wos_downloads/aggregated'
for root, dirs, files in os.walk(workdir_path):
    for filename in files:
        if 'analyze_' in filename:
            path=os.path.join(root, filename)
            with open(os.path.join(root, 'query.txt'),'r') as f:
                query = f.readline()
            try:
                chunk = pd.read_csv(path, sep='\t')[["Publication Years","Record Count"]]
            except EmptyDataError:
                path=os.path.join(root, "analyze.txt")
                chunk = pd.read_csv(path, sep='\t')[["Publication Years","Record Count"]]
            chunk["name"] = filename.replace(".txt","")
            chunk["query"] = query
            agg_df = pd.concat([chunk,agg_df],ignore_index=True)
        # elif len(files)==1:


In [17]:
agg_df["region"] = agg_df["query"].apply(lambda x: "EU+China" if "CU" in x else "Global")
agg_df["kw_token"] = agg_df["query"].apply(lambda x: x.split("TS=(")[-1].split(")")[0].strip("("))
agg_df["kw_token"] = agg_df["kw_token"].apply(lambda x: "COMPOSITE SEARCH" if " OR " in x else x)

In [18]:
agg_df = agg_df[~agg_df["Record Count"].isna()]

In [19]:
agg_df.groupby("query",as_index=False)["Record Count"].sum()

query  Record Count
0    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...         972.0
1    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...         451.0
2    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...          30.0
3    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...          12.0
4    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...           5.0
..                                                 ...           ...
543  TS=(("face recognition" NOT "brain")) AND PY=(...       19690.0
544  TS=(("linear regression" NOT "p=")) AND PY=(20...       91493.0
545  TS=(("logistic regression" NOT "p=")) AND PY=(...      171776.0
546  TS=(("object detection" NOT "brain")) AND PY=(...       28989.0
547  TS=(("speech recognition" NOT "brain")) AND PY...       19912.0

[548 rows x 2 columns]

In [29]:
kw_ranks = agg_df[agg_df["region"]=="EU+China"].groupby("kw_token",as_index=False)["Record Count"].sum().sort_values(by="Record Count", ascending=False).reset_index().drop(columns="index")
kw_ranks

kw_token  Record Count
0               COMPOSITE SEARCH       62205.0
1              "neural network*"       10999.0
2              "machine* learn*"        5765.0
3                  "deep learn*"        5211.0
4                     "momentum"        4974.0
..                           ...           ...
243       "artificial cognition"           1.0
244  "ai in disaster management"           1.0
245          "vector embedding*"           1.0
246              "ai in finance"           1.0
247    "content based filtering"           1.0

[248 rows x 2 columns]

In [30]:
kw_ranks.to_excel("kw_token_ranked.xlsx")

In [21]:
# agg_df = agg_df[agg_df["Publication Years"].str.startswith("20", na=False)].copy()
# agg_df["Publication Years"] = agg_df["Publication Years"].astype(int)
# agg_df[((agg_df["Publication Years"]>2010) & (agg_df["Publication Years"]<2023))]

In [22]:
# agg_df["Publication Years"].value_counts()

In [23]:
agg_df.to_excel(r'C:\Users\radvanyi\PycharmProjects\ZSI_analytics\WOS\wos_processed_data\query_yearly_agg.xlsx', index=False)